1. 열린데이터광장 > 서울시 따릉이 대여소별 대여/반납 승객수 정보   
https://data.seoul.go.kr/dataList/OA-21229/F/1/datasetView.do   
2. 열린데이터광장 > 서울특별시_따릉이대여소 마스터 정보    
https://www.data.go.kr/data/15099365/fileData.do  
3. 서울시 빅데이터 캠퍼스 > 서울시 행정동별 내국인 KT 생활이동 데이터   
https://bigdata.seoul.go.kr/data/selectSampleData.do?r_id=P213&sample_data_seq=330&tab_type=&file_id=1651221780698P6PK6ELBSNSRZGLRH94502KIH&sch_text=%EC%9D%B4%EB%8F%99&sch_order=U&currentPage=1  
4. 서울시 자전거 도로 데이터 
5. 서울시 경사 데이터  

## 지하철 데이터 제공의 지연으로, 이미 제공된 '따릉이 데이터' 활용하여 분석 예정  
### 1. 따릉이 계절별/시간대별 대여 및 반납 분석을 통해 따릉이 배치 제안 
### 2. 따릉이 대여/반납 장소 데이터를 통해 자전거 도로의 확충이 필요한 지역 분석 
### 3. 따릉이 및 유동인구 데이터 분석을 통해 퀵보드 주차장 입지 선정  

In [19]:
import pandas as pd
import numpy as np
import matplotlib
import matplotlib.pyplot as plt

import os

### bicycle 데이터 월별 zip 파일 불러와서 합치기  

In [18]:
# zip 파일 풀기 
import zipfile
         
fantasy_zip = zipfile.ZipFile('tpss_bcycl_od_statnhm_202205.zip')
fantasy_zip.extractall('./bicycle_202205')
 
fantasy_zip.close()

In [20]:
# 한달어치의 csv 파일 불러오기  

dir_path = "./bicycle_202205"
file_paths=[]

for (root, directories, files) in os.walk(dir_path):
    for file in files:
        if '.csv' in file:
            file_path = os.path.join(root, file)
            file_paths.append(file_path)

In [22]:
# 한달어치의 csv 파일 -> data merge 
colnames=['기준_날짜', '기준_시간대', '시작_대여소_ID', '종료_대여소_ID', '전체_건수', '전체_이용_분', '전체_이용_거리']

bicycle_df = []
for path in file_paths:
    bicycle_tmp=pd.read_csv(path,encoding='cp949')
    bicycle_tmp.columns=colnames
    bicycle_df.append(bicycle_tmp)
    
bicycle=pd.concat(bicycle_df, axis=0, ignore_index=True)
bicycle

기준_날짜  기준_시간대 시작_대여소_ID 종료_대여소_ID  전체_건수  전체_이용_분  전체_이용_거리
0        20220517       0   ST-1017   ST-1495      1        4       640
1        20220517       0   ST-1019    ST-282      1        6      1106
2        20220517       0   ST-1020    ST-479      1        6      1147
3        20220517       0   ST-1025    ST-465      1        5       670
4        20220517       0   ST-1041   ST-1041      1       21       180
...           ...     ...       ...       ...    ...      ...       ...
9290660  20220526    2355   ST-1413   ST-1408      1        4       381
9290661  20220526    2355   ST-2266   ST-2266      1        1         0
9290662  20220526    2355   ST-2865   ST-2865      1        1         0
9290663  20220526    2355   ST-3060   ST-3060      1        0         0
9290664  20220526    2355   ST-1866   ST-1866      1        0         0

[9290665 rows x 7 columns]

In [26]:
import datetime

# 전체_이용_분 = 0, 전체_이용_거리 = 0, 시작_대여소=종료_대여소 인 데이터는 제거
bicycle=bicycle[(bicycle["전체_이용_분"]>0) & (bicycle["전체_이용_거리"]>0)]
bicycle=bicycle[bicycle["시작_대여소_ID"]!=bicycle["종료_대여소_ID"]]

# 뒤에서 대여소 위치 데이터와 merge 위해서 형태 변경 
bicycle['시작_대여소_ID'] = bicycle['시작_대여소_ID'].str.split('-').str[1]
bicycle['종료_대여소_ID'] = bicycle['종료_대여소_ID'].str.split('-').str[1]
bicycle = bicycle.iloc[:,:4]

# 날짜랑 시간 datetime 형식으로 변경 
bicycle['기준_시간대']=bicycle['기준_시간대'].apply(lambda x: str(x).zfill(4))
day_time=bicycle['기준_날짜'].astype(str)+bicycle['기준_시간대']
bicycle['기준_날짜시간']=pd.to_datetime(day_time,format="%Y%m%d%H%M")

# 요일값 추가 
days=['월','화','수','목','금','토','일']
bicycle['weekday']=bicycle['기준_날짜시간'].dt.weekday
bicycle['요일']=bicycle.apply(lambda x: days[x['weekday']], axis=1)

bicycle=bicycle.iloc[:,2:]
bicycle.drop('weekday', axis=1, inplace=True)

bicycle.sort_values('기준_날짜시간',inplace=True)
bicycle.reset_index(drop=True,inplace=True)

bicycle['시작_대여소_ID']=bicycle['시작_대여소_ID'].astype(int)
bicycle['종료_대여소_ID']=bicycle['종료_대여소_ID'].astype(int)

bicycle

시작_대여소_ID  종료_대여소_ID             기준_날짜시간  weekday 요일
0             1002       1700 2022-05-01 00:00:00        6  일
1              378       2314 2022-05-01 00:00:00        6  일
2              377        258 2022-05-01 00:00:00        6  일
3              369       2226 2022-05-01 00:00:00        6  일
4              369       1200 2022-05-01 00:00:00        6  일
...            ...        ...                 ...      ... ..
8166428       1689       2037 2022-05-31 23:55:00        1  화
8166429       1683       1626 2022-05-31 23:55:00        1  화
8166430       1678        702 2022-05-31 23:55:00        1  화
8166431       1725        647 2022-05-31 23:55:00        1  화
8166432       1967       2902 2022-05-31 23:55:00        1  화

[8166433 rows x 5 columns]

. . . 데이터 합치는 것 까지 완료 

### 동별 출발지 횟수, 도착지 횟수 - 지도시각화

In [42]:
# 대한민국 행정동 중 서울특별시 행정동만 추출 
import json
with open('HangJeongDong220701.txt') as f:
    json_d = json.load(f)

new_features=[]
for lst in json_d.get('features'):
    if '서울특별시' in lst.get('properties')['adm_nm']:
        new_features.append(lst)
        
json_d['features']=new_features
json_d

{'type': 'FeatureCollection',
 'name': '20220701',
 'crs': {'type': 'name',
  'properties': {'name': 'urn:ogc:def:crs:OGC:1.3:CRS84'}},
 'features': [{'type': 'Feature',
   'properties': {'OBJECTID': 1,
    'adm_nm': '서울특별시 종로구 사직동',
    'adm_cd': '1101053',
    'adm_cd2': '1111053000',
    'sgg': '11110',
    'sido': '11',
    'sidonm': '서울특별시',
    'sggnm': '종로구',
    'adm_cd8': '11010530'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[126.97688884274817, 37.575650779448786],
       [126.9770344988775, 37.56919453005455],
       [126.97597472821249, 37.569336299425764],
       [126.97537470991254, 37.56931556702156],
       [126.97433193562325, 37.56926180051753],
       [126.96904837001854, 37.568194417708334],
       [126.96854493603384, 37.56842767961276],
       [126.9666499598212, 37.56949165520658],
       [126.96628175024485, 37.5697007347987],
       [126.9660973270804, 37.5698565097237],
       [126.96572852922577, 37.570183936115114],
       [126.965926998

. . . 진행중 

----------

In [43]:
location=pd.read_csv("./data/bicycle_location.csv",encoding='cp949')
bicycle=pd.read_csv("./data/tpss_bcycl_od_statnhm_20220531.csv",encoding='cp949')
walk=pd.read_csv("./data/WALK_08_29__9_4.csv",encoding='cp949')

In [44]:
location=location.iloc[:,[0,3,4]]
location['좌표']=list(zip(location['위도'].round(6),location['위도'].round(6)))
location

대여소ID         위도          경도                      좌표
0         2   0.000000    0.000000              (0.0, 0.0)
1         3  37.549561  126.905754  (37.549561, 37.549561)
2         4  37.555649  126.910629  (37.555649, 37.555649)
3         5  37.554951  126.910835  (37.554951, 37.554951)
4         6  37.550629  126.914986  (37.550629, 37.550629)
...     ...        ...         ...                     ...
3128   3140  37.556877  126.936035  (37.556877, 37.556877)
3129   3141  37.539139  127.121620  (37.539139, 37.539139)
3130   3142  37.516693  126.908073  (37.516693, 37.516693)
3131   3143  37.472202  126.933907  (37.472202, 37.472202)
3132   3144  37.482853  127.005974  (37.482853, 37.482853)

[3133 rows x 4 columns]

In [45]:
bicycle['시작_대여소_ID'] = bicycle['시작_대여소_ID'].str.split('-').str[1]
bicycle['종료_대여소_ID'] = bicycle['종료_대여소_ID'].str.split('-').str[1]
bicycle = bicycle.iloc[:,:4]
bicycle=bicycle[bicycle["시작_대여소_ID"]!=bicycle["종료_대여소_ID"]]

bicycle['기준_시간대']=bicycle['기준_시간대'].apply(lambda x: str(x).zfill(4))
day_time=bicycle['기준_날짜'].astype(str)+bicycle['기준_시간대']
bicycle['기준_날짜시간']=pd.to_datetime(day_time,format="%Y%m%d%H%M")
bicycle=bicycle.iloc[:,2:]

bicycle.sort_values('기준_날짜시간',inplace=True)
bicycle.reset_index(drop=True,inplace=True)

bicycle['시작_대여소_ID']=bicycle['시작_대여소_ID'].astype(int)
bicycle['종료_대여소_ID']=bicycle['종료_대여소_ID'].astype(int)

bicycle

시작_대여소_ID  종료_대여소_ID             기준_날짜시간
0            1006       2770 2022-05-31 00:00:00
1             371       2331 2022-05-31 00:00:00
2             360        189 2022-05-31 00:00:00
3             338        175 2022-05-31 00:00:00
4             330        437 2022-05-31 00:00:00
...           ...        ...                 ...
303210        645       2136 2022-05-31 23:55:00
303211        644       1105 2022-05-31 23:55:00
303212         64       2669 2022-05-31 23:55:00
303213        605       2703 2022-05-31 23:55:00
303214        646       2137 2022-05-31 23:55:00

[303215 rows x 3 columns]

In [46]:
bicycle_location=pd.merge(bicycle, location, how='left', left_on='시작_대여소_ID', right_on='대여소ID')
bicycle_location.rename(columns={'좌표':'시작_좌표'},inplace=True)
bicycle_location=pd.merge(bicycle_location, location, how='left', left_on='종료_대여소_ID', right_on='대여소ID')
bicycle_location.rename(columns={'좌표':'종료_좌표'},inplace=True)
bicycle_location=bicycle_location.iloc[:,[2,4,5,6,8,9,10]]
bicycle_location

기준_날짜시간       위도_x        경도_x                   시작_좌표  \
0      2022-05-31 00:00:00  37.536377  126.871513  (37.536377, 37.536377)   
1      2022-05-31 00:00:00  37.548290  127.062462    (37.54829, 37.54829)   
2      2022-05-31 00:00:00  37.561096  127.036797  (37.561096, 37.561096)   
3      2022-05-31 00:00:00  37.566994  127.003464  (37.566994, 37.566994)   
4      2022-05-31 00:00:00  37.530167  127.007439  (37.530167, 37.530167)   
...                    ...        ...         ...                     ...   
303210 2022-05-31 23:55:00  37.640327  127.013359  (37.640327, 37.640327)   
303211 2022-05-31 23:55:00  37.624157  127.018623  (37.624157, 37.624157)   
303212 2022-05-31 23:55:00  37.524837  126.934906  (37.524837, 37.524837)   
303213 2022-05-31 23:55:00  37.635109  127.068329  (37.635109, 37.635109)   
303214 2022-05-31 23:55:00  37.638805  127.028358  (37.638805, 37.638805)   

             위도_y        경도_y                   종료_좌표  
0       37.520916  126.840958  (37.520916, 37.520916)  
1       37.555141  127.071106  (37.555141, 37.555141)  
2       37.560474  127.014076  (37.560474, 37.560474)  
3       37.573242  127.015907  (37.573242, 37.573242)  
4       37.544895  126.969383  (37.544895, 37.544895)  
...           ...         ...                     ...  
303210  37.647934  127.014572  (37.647934, 37.647934)  
303211  37.613956  127.030251  (37.613956, 37.613956)  
303212  37.481167  126.997589  (37.481167, 37.481167)  
303213  37.632145  127.069824  (37.632145, 37.632145)  
303214  37.637970  127.025902    (37.63797, 37.63797)  

[303215 rows x 7 columns]

In [47]:
# 시작 - 도착 경로 
graph1=pd.pivot_table(bicycle_location,index=["위도_x","경도_x","위도_y","경도_y","시작_좌표","종료_좌표"],aggfunc='count')
graph1.reset_index(inplace=True)
graph1.rename(columns={'기준_날짜시간':'횟수'},inplace=True)
graph1

위도_x        경도_x       위도_y        경도_y                   시작_좌표  \
0      37.430977  127.070335  37.447659  127.055016  (37.430977, 37.430977)   
1      37.430977  127.070335  37.454357  127.062103  (37.430977, 37.430977)   
2      37.430977  127.070335  37.457226  127.059006  (37.430977, 37.430977)   
3      37.430977  127.070335  37.475605  127.050377  (37.430977, 37.430977)   
4      37.430977  127.070335  37.482979  127.042259  (37.430977, 37.430977)   
...          ...         ...        ...         ...                     ...   
88317  37.691013  127.049164  37.668671  127.047981  (37.691013, 37.691013)   
88318  37.691013  127.049164  37.674366  127.059471  (37.691013, 37.691013)   
88319  37.691013  127.049164  37.677219  127.048637  (37.691013, 37.691013)   
88320  37.691013  127.049164  37.679848  127.050385  (37.691013, 37.691013)   
88321  37.691013  127.049164  37.685234  127.049858  (37.691013, 37.691013)   

                        종료_좌표  횟수  
0      (37.447659, 37.447659)   4  
1      (37.454357, 37.454357)   2  
2      (37.457226, 37.457226)   2  
3      (37.475605, 37.475605)   2  
4      (37.482979, 37.482979)   2  
...                       ...  ..  
88317  (37.668671, 37.668671)   7  
88318  (37.674366, 37.674366)   2  
88319  (37.677219, 37.677219)   2  
88320  (37.679848, 37.679848)   8  
88321  (37.685234, 37.685234)   2  

[88322 rows x 7 columns]

In [ ]:
print(graph1['횟수'].sort_values().unique())
np.percentile(graph1['횟수'].sort_values().unique(),[25,50,75],interpolation='nearest')

[ 1  2  3  4  5  6  7  8  9 10 11 12 13 14 15 16 17 18 19 20 21 22 23 24
 25 26 27 28 29 30 31 32 33 34 35 36 37 38 39 40 41 42 43 44 46 47 48 49
 50 51 52 53 54 55 56 57 58 59 60 61 63 64 65 67 68 69 71 82 86]


array([18, 35, 53])

In [ ]:
graph1_25=graph1[graph1['횟수']<18]
graph1_50=graph1[(graph1['횟수']>=18) & (graph1['횟수']<35)]
graph1_75=graph1[(graph1['횟수']>=35) & (graph1['횟수']<53)]
graph1_100=graph1[graph1['횟수']>=53]

In [ ]:
import folium
center = [37.541, 126.986]
mapp = folium.Map(location=center, zoom_start=11)

folium.PolyLine(
    locations = [list(zip(graph1_25['위도_x'],graph1_25['경도_x'])),list(zip(graph1_25['위도_y'],graph1_25['경도_y']))],
    opacity = 0.3 , color='red'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_50['위도_x'],graph1_50['경도_x'])),list(zip(graph1_50['위도_y'],graph1_50['경도_y']))],
    opacity = 0.3 , color='green'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_75['위도_x'],graph1_75['경도_x'])),list(zip(graph1_75['위도_y'],graph1_75['경도_y']))],
    opacity = 0.3 , color='blue'
).add_to(mapp)
folium.PolyLine(
    locations = [list(zip(graph1_100['위도_x'],graph1_100['경도_x'])),list(zip(graph1_100['위도_y'],graph1_100['경도_y']))],
    opacity = 0.3 , color='purple'
).add_to(mapp)
mapp